In [11]:
import pandas as pd
import numpy as np
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_absolute_error, mean_squared_error, explained_variance_score, median_absolute_error, r2_score, mean_absolute_percentage_error
from sklearn.model_selection import train_test_split
from scipy.stats import *
import h3
from sklearn.preprocessing import OneHotEncoder
from sklearn.compose import ColumnTransformer
from datetime import datetime

In [12]:
ride_columns = ['accepted_driver_id', 'created_at', 'passenger_id', 'source_lat',
       'source_lng', 'destination_lat', 'destination_lng', 'eta', 'provider',
       'ata', 'id', 'city']

khatkesh_columns = ['ride_id','driver_id','a_t_a_result.arrival_a_t_a','a_t_a_result.boarding_a_t_a','a_t_a_result.ride_a_t_a','a_t_a_result.arrival_probe_result.probe.point.lat','a_t_a_result.arrival_probe_result.probe.point.lon','a_t_a_result.arrival_probe_result.probe.timestamp','a_t_a_result.arrival_probe_result.confidence','a_t_a_result.arrival_probe_result.h3_index', 'a_t_a_result.arrival_probe_result.k_ring_level','a_t_a_result.boarding_probe_result.probe.point.lat','a_t_a_result.boarding_probe_result.probe.point.lon','a_t_a_result.boarding_probe_result.probe.timestamp','a_t_a_result.boarding_probe_result.confidence','a_t_a_result.boarding_probe_result.h3_index','a_t_a_result.boarding_probe_result.k_ring_level','a_t_a_result.final_destination_probe_result.probe.point.lat','a_t_a_result.final_destination_probe_result.probe.point.lon','a_t_a_result.final_destination_probe_result.probe.timestamp','a_t_a_result.final_destination_probe_result.confidence','a_t_a_result.final_destination_probe_result.h3_index','a_t_a_result.final_destination_probe_result.k_ring_level','a_t_a_result.destination_probe_result.probe.point.lat','a_t_a_result.destination_probe_result.probe.point.lon','a_t_a_result.destination_probe_result.probe.timestamp','a_t_a_result.destination_probe_result.confidence','a_t_a_result.destination_probe_result.h3_index','a_t_a_result.destination_probe_result.k_ring_level','a_t_a_result.extra_destination_probe_result.probe.point.lat','a_t_a_result.extra_destination_probe_result.probe.point.lon','a_t_a_result.extra_destination_probe_result.probe.timestamp','a_t_a_result.extra_destination_probe_result.confidence','a_t_a_result.extra_destination_probe_result.h3_index','a_t_a_result.extra_destination_probe_result.k_ring_level','pickup_a_d_d_result.distance','pickup_a_d_d_result.confidence','pickup_a_d_d_result.route_ratio','pickup_a_d_d_result.g_p_s_ratio','ride_a_d_d_result.distance','ride_a_d_d_result.confidence','ride_a_d_d_result.route_ratio','ride_a_d_d_result.g_p_s_ratio','total_a_d_d_confidence','in_ride_allotment','e_d_d','clickhouse_time','hash']

dates = ['2022-09-03', '2022-09-04', '2022-09-05' , '2022-09-06', '2022-09-07', '2022-09-08', '2022-09-09',
         '2022-09-10', '2022-09-11', '2022-09-12', '2022-09-13', '2022-09-14', '2022-09-15', '2022-09-16']


In [13]:
# rides = pd.read_csv("../rides_oct_04.csv", names=ride_columns)
# rides.rename(columns={'id': 'ride_id'}, inplace=True)
# rides.describe()

In [14]:
for iddate, date in enumerate(dates):
    rides_df = pd.read_csv('../rides_' + date + '.csv', names=ride_columns)
    rides_df.rename(columns={'id': 'ride_id'}, inplace=True)

    files = ['../khatkesh_' + date + '_.csv']
    if iddate+1 != len(dates):
        files.append('../khatkesh_' + dates[iddate+1] + '_.csv')
    # THE IGNORE INDEX IS WRONG MAYBE
    khatkesh_df = pd.concat((pd.read_csv(f, names=khatkesh_columns) for f in files), ignore_index=True)

    rides_khatkesh = pd.merge(rides_df, khatkesh_df, on="ride_id")

    print(len(rides_df))
    print(date)
    print(len(rides_khatkesh))

    rides_khatkesh.to_csv('../ride_khatkesh.csv', mode='a')

110997
2022-09-03
110791
119252
2022-09-04
82345
124816
2022-09-05
115489
122900
2022-09-06
122904
137370
2022-09-07
121009
116512
2022-09-08
52416
66165
2022-09-09
19511
119866
2022-09-10
119862
136315
2022-09-11
108684
124424
2022-09-12
124424
122852
2022-09-13
86612
129746
2022-09-14
119049
110708
2022-09-15
110650
64312
2022-09-16
62664


In [15]:
# khatkesh = pd.read_csv("../khatkesh_oct_04.csv", names=khatkesh_columns)
# khatkesh.describe()

In [16]:
# rides_khatkesh = pd.merge(rides, khatkesh, on="ride_id")
# rides_khatkesh.describe()

In [17]:
rides_khatkesh = pd.read_csv('../ride_khatkesh.csv')

/var/folders/yq/707ysz_j3jlggmtk5clx13rm0000gn/T/ipykernel_33110/4000924381.py:1: DtypeWarning: Columns (1,3,4,5,6,7,8,10,11,12,13,14,15,16,17,18,19,20,22,23,24,25,26,28,29,30,31,32,34,35,36,37,38,40,41,42,43,44,45,46,47,48,49,50,51,52,53,54,55,56,57,59) have mixed types. Specify dtype option on import or set low_memory=False.
  rides_khatkesh =pd.read_csv('../ride_khatkesh.csv')


In [30]:
rides_khatkesh = rides_khatkesh[rides_khatkesh['Unnamed: 0'].isna() == False]

In [43]:
for e in rides_khatkesh['eta']:
    if type(e) != int:
        print(e)
        print(type(e))


610
<class 'str'>
3641
<class 'str'>
1836
<class 'str'>
347
<class 'str'>
2874
<class 'str'>
893
<class 'str'>
1004
<class 'str'>
747
<class 'str'>
669
<class 'str'>
1508
<class 'str'>
473
<class 'str'>
2898
<class 'str'>
1460
<class 'str'>
2510
<class 'str'>
354
<class 'str'>
3950
<class 'str'>
691
<class 'str'>
1183
<class 'str'>
458
<class 'str'>
651
<class 'str'>
1047
<class 'str'>
1942
<class 'str'>
1011
<class 'str'>
1188
<class 'str'>
677
<class 'str'>
1771
<class 'str'>
638
<class 'str'>
981
<class 'str'>
1859
<class 'str'>
210
<class 'str'>
688
<class 'str'>
680
<class 'str'>
1138
<class 'str'>
1498
<class 'str'>
1157
<class 'str'>
861
<class 'str'>
2409
<class 'str'>
175
<class 'str'>
1888
<class 'str'>
405
<class 'str'>
461
<class 'str'>
265
<class 'str'>
460
<class 'str'>
266
<class 'str'>
354
<class 'str'>
833
<class 'str'>
710
<class 'str'>
951
<class 'str'>
1111
<class 'str'>
227
<class 'str'>
983
<class 'str'>
1969
<class 'str'>
219
<class 'str'>
585
<class 'str'>
193
<

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [44]:
rides_khatkesh.to_csv('../ride_khatkesh_1.csv')

rides_khatkesh = pd.read_csv('../ride_khatkesh_1.csv')

In [45]:
rides_khatkesh.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1356410 entries, 0 to 1356409
Data columns (total 61 columns):
 #   Column                                                       Non-Null Count    Dtype  
---  ------                                                       --------------    -----  
 0   Unnamed: 0.1                                                 1356410 non-null  int64  
 1   Unnamed: 0                                                   1356410 non-null  float64
 2   accepted_driver_id                                           1356410 non-null  int64  
 3   created_at                                                   1356410 non-null  object 
 4   passenger_id                                                 1356410 non-null  int64  
 5   source_lat                                                   1356410 non-null  float64
 6   source_lng                                                   1356410 non-null  float64
 7   destination_lat                                       

In [46]:
rides = rides_khatkesh[(rides_khatkesh['eta'] > 180) &
                       (rides_khatkesh['eta'] < 10800) &
                       (rides_khatkesh['a_t_a_result.ride_a_t_a'] > 180) &
                       (rides_khatkesh['a_t_a_result.ride_a_t_a'] < 10800)]
rides.describe()

Unnamed: 0.1    Unnamed: 0  accepted_driver_id  passenger_id  \
count  1.304773e+06  1.304773e+06        1.304773e+06  1.304773e+06   
mean   6.776261e+05  5.335049e+04        1.887709e+06  2.312404e+07   
std    3.917375e+05  3.332452e+04        1.436909e+06  1.807453e+07   
min    0.000000e+00  0.000000e+00        0.000000e+00  3.800000e+01   
25%    3.381880e+05  2.457100e+04        4.385930e+05  4.471473e+06   
50%    6.769530e+05  5.063700e+04        1.779187e+06  2.294847e+07   
75%    1.016971e+06  8.023200e+04        3.201126e+06  3.773902e+07   
max    1.356422e+06  1.244230e+05        4.350712e+06  5.758165e+07   

         source_lat    source_lng  destination_lat  destination_lng  \
count  1.304773e+06  1.304773e+06     1.304773e+06     1.304773e+06   
mean   3.569881e+01  5.140256e+01     3.570100e+01     5.139414e+01   
std    8.998554e-02  1.301368e-01     9.047574e-02     1.421605e-01   
min    3.518616e+01  5.090034e+01     3.452721e+01     4.985955e+01   
25%    3.567223e+01  5.133963e+01     3.567519e+01     5.133597e+01   
50%    3.572297e+01  5.140762e+01     3.572369e+01     5.140681e+01   
75%    3.575577e+01  5.146061e+01     3.575684e+01     5.145822e+01   
max    3.583987e+01  5.282693e+01     3.646163e+01     5.340880e+01   

                eta           ata  ...  pickup_a_d_d_result.route_ratio  \
count  1.304773e+06  1.304773e+06  ...                     1.304773e+06   
mean   1.046471e+03  1.212058e+03  ...                     1.521520e-04   
std    7.314098e+02  9.865582e+02  ...                     9.815981e-03   
min    1.810000e+02  1.200000e+02  ...                     0.000000e+00   
25%    5.240000e+02  5.470000e+02  ...                     0.000000e+00   
50%    8.560000e+02  9.320000e+02  ...                     0.000000e+00   
75%    1.349000e+03  1.552000e+03  ...                     0.000000e+00   
max    1.055900e+04  2.709500e+04  ...                     1.000000e+00   

       pickup_a_d_d_result.g_p_s_ratio  ride_a_d_d_result.distance  \
count                     1.304773e+06                1.304773e+06   
mean                      1.220451e-02                1.922243e+01   
std                       9.958596e-03                1.894511e+01   
min                       0.000000e+00                0.000000e+00   
25%                       5.263158e-03                6.708000e+00   
50%                       9.523810e-03                1.356200e+01   
75%                       1.666667e-02                2.485989e+01   
max                       5.263158e-02                1.344062e+03   

       ride_a_d_d_result.confidence  ride_a_d_d_result.route_ratio  \
count                  1.304773e+06                   1.304773e+06   
mean                   8.722293e-01                   4.876285e-05   
std                    1.746976e-01                   1.562254e-03   
min                    0.000000e+00                   0.000000e+00   
25%                    8.000000e-01                   0.000000e+00   
50%                    9.625540e-01                   0.000000e+00   
75%                    1.000000e+00                   0.000000e+00   
max                    1.000000e+00                   2.357488e-01   

       ride_a_d_d_result.g_p_s_ratio  total_a_d_d_confidence  \
count                   1.304773e+06            1.304773e+06   
mean                    7.477702e-01            8.807183e-01   
std                     3.280260e-01            1.654017e-01   
min                     0.000000e+00            0.000000e+00   
25%                     5.862069e-01            8.232145e-01   
50%                     9.230769e-01            9.624756e-01   
75%                     9.888889e-01            1.000000e+00   
max                     1.000000e+00            1.000000e+00   

       in_ride_allotment         e_d_d          hash  
count       1.304773e+06  1.304773e+06  1.304773e+06  
mean        2.221006e-02  1.156276e+01  9.223152e+18  
std         2.185958e-01  1.170856e+01  5.32185

In [47]:
rides = rides[rides['ride_a_d_d_result.confidence'] > 0.6]
rides.describe()

Unnamed: 0.1    Unnamed: 0  accepted_driver_id  passenger_id  \
count  1.122161e+06  1.122161e+06        1.122161e+06  1.122161e+06   
mean   6.771143e+05  5.339750e+04        1.905365e+06  2.314064e+07   
std    3.921005e+05  3.330513e+04        1.440748e+06  1.806817e+07   
min    0.000000e+00  0.000000e+00        0.000000e+00  3.800000e+01   
25%    3.371850e+05  2.465700e+04        4.491760e+05  4.487216e+06   
50%    6.769710e+05  5.070000e+04        1.809660e+06  2.299294e+07   
75%    1.017076e+06  8.025700e+04        3.225940e+06  3.776165e+07   
max    1.356422e+06  1.244220e+05        4.350712e+06  5.758165e+07   

         source_lat    source_lng  destination_lat  destination_lng  \
count  1.122161e+06  1.122161e+06     1.122161e+06     1.122161e+06   
mean   3.569854e+01  5.140213e+01     3.570073e+01     5.139398e+01   
std    9.024166e-02  1.307453e-01     9.043371e-02     1.422515e-01   
min    3.518616e+01  5.090034e+01     3.452721e+01     4.992399e+01   
25%    3.567175e+01  5.133850e+01     3.567473e+01     5.133565e+01   
50%    3.572295e+01  5.140703e+01     3.572367e+01     5.140628e+01   
75%    3.575573e+01  5.146032e+01     3.575677e+01     5.145801e+01   
max    3.583967e+01  5.282693e+01     3.646163e+01     5.281060e+01   

                eta           ata  ...  pickup_a_d_d_result.route_ratio  \
count  1.122161e+06  1.122161e+06  ...                     1.122161e+06   
mean   1.036433e+03  1.200448e+03  ...                     1.092608e-04   
std    7.237808e+02  9.760965e+02  ...                     8.078303e-03   
min    1.810000e+02  1.200000e+02  ...                     0.000000e+00   
25%    5.190000e+02  5.430000e+02  ...                     0.000000e+00   
50%    8.470000e+02  9.230000e+02  ...                     0.000000e+00   
75%    1.336000e+03  1.536000e+03  ...                     0.000000e+00   
max    9.199000e+03  2.301700e+04  ...                     1.000000e+00   

       pickup_a_d_d_result.g_p_s_ratio  ride_a_d_d_result.distance  \
count                     1.122161e+06                1.122161e+06   
mean                      1.304499e-02                2.014186e+01   
std                       9.942246e-03                1.936953e+01   
min                       0.000000e+00                1.000000e-01   
25%                       5.952381e-03                7.162000e+00   
50%                       1.020408e-02                1.446800e+01   
75%                       1.754386e-02                2.607400e+01   
max                       5.263158e-02                2.794880e+02   

       ride_a_d_d_result.confidence  ride_a_d_d_result.route_ratio  \
count                  1.122161e+06                   1.122161e+06   
mean                   9.307232e-01                   2.833662e-05   
std                    1.009482e-01                   1.121238e-03   
min                    6.000000e-01                   0.000000e+00   
25%                    9.031330e-01                   0.000000e+00   
50%                    9.791426e-01                   0.000000e+00   
75%                    1.000000e+00                   0.000000e+00   
max                    1.000000e+00                   2.357488e-01   

       ride_a_d_d_result.g_p_s_ratio  total_a_d_d_confidence  \
count                   1.122161e+06            1.122161e+06   
mean                    8.444126e-01            9.356969e-01   
std                     2.204519e-01            9.135201e-02   
min                     0.000000e+00            6.431787e-02   
25%                     7.941176e-01            9.035648e-01   
50%                     9.486803e-01            9.779251e-01   
75%                     9.950000e-01            1.000000e+00   
max                     1.000000e+00            1.000000e+00   

       in_ride_allotment         e_d_d          hash  
count       1.122161e+06  1.122161e+06  1.122161e+06  
mean        2.491458e-02  1.140162e+01  9.222249e+18  
std         2.301024e-01  1.149971e+01  5.32199

In [48]:
rides = rides[['eta', 'ata', 'a_t_a_result.ride_a_t_a', 'created_at', 'source_lat', 'source_lng', 'destination_lat', 'destination_lng', 'e_d_d', 'clickhouse_time']]
rides

eta   ata  a_t_a_result.ride_a_t_a           created_at  source_lat  \
0         285   276                      288  2022-09-03 16:49:38   35.701385   
1        2090  2420                     2414  2022-09-03 13:05:36   35.712814   
2         457   371                      359  2022-09-03 21:40:08   35.747662   
3        2123  3890                     2920  2022-09-03 17:34:40   35.734798   
4         272   302                      290  2022-09-03 20:55:37   35.497204   
...       ...   ...                      ...                  ...         ...   
1356405   641   523                      500  2022-09-16 22:20:51   35.692471   
1356406   962   920                      886  2022-09-16 21:48:34   35.760612   
1356407  1338  1972                     1692  2022-09-16 12:43:04   35.709476   
1356408  1984  1944                     1931  2022-09-16 05:42:47   35.768810   
1356409   448   457                      437  2022-09-16 10:23:48   35.680775   

         source_lng  destination_lat  destination_lng      e_d_d  \
0         51.418598        35.697102        51.428875   1.791000   
1         51.375633        35.741585        51.065804  37.113998   
2         51.800034        35.755596        51.802029   3.564000   
3         51.386841        35.668949        51.365444  13.958000   
4         51.229351        35.504349        51.224445   1.868000   
...             ...              ...              ...        ...   
1356405   51.485405        35.678619        51.464706   3.449000   
1356406   51.427483        35.716057        51.451225   8.640000   
1356407   51.349098        35.813549        51.430065  17.261999   
1356408   51.302879        35.815525        50.971333  42.470001   
1356409   51.397083        35.698784        51.400398   3.114000   

             clickhouse_time  
0        2022-09-03 16:57:01  
1        2022-09-03 14:12:31  
2        2022-09-03 21:49:52  
3        2022-09-03 18:47:51  
4        2022-09-03 21:03:36  
...                      ...  
1356405  2022-09-16 23:09:24  
1356406  2022-09-16 22:43:34  
1356407  2022-09-16 13:25:15  
1356408  2022-09-16 06:27:14  
1356409  2022-09-16 10:38:11  

[1122161 rows x 10 columns]

In [49]:
rides['source_h3_4'] = rides.apply(lambda row: h3.geo_to_h3(row.source_lat, row.source_lng, 4), axis=1)
rides['dest_h3_4'] = rides.apply(lambda row: h3.geo_to_h3(row.destination_lat, row.destination_lng, 4), axis=1)

In [51]:
timestamp = datetime.timestamp(datetime.strptime(rides.created_at[0],"%Y-%m-%d %H:%M:%S"))
print("timestamp =", timestamp)

timestamp = 1662207578.0


In [52]:
((1662207578 - 1662147000) % 604800) / 3600

16.827222222222222

In [53]:
rides.created_at[0]

'2022-09-03 16:49:38'

In [54]:
# WE WERE HERE
rides.apply(lambda row: ((datetime.timestamp(datetime.strptime(row.created_at,"%Y-%m-%d %H:%M:%S")) - 1662147000) % 604800) / 3600, axis=1)

0           16.827222
1           13.093333
2           21.668889
3           17.577778
4           20.926944
              ...    
1356405    166.347500
1356406    165.809444
1356407    156.717778
1356408    149.713056
1356409    154.396667
Length: 1122161, dtype: float64

In [9]:
rides['hour'] = rides.apply(lambda row: datetime.strptime(row.created_at,"%Y-%m-%d %H:%M:%S").hour, axis=1)

In [10]:
# eta_edd_h3_hour = rides[["eta", "e_d_d", "source_h3_4", "dest_h3_4", "hour"]]
# ata = rides["a_t_a_result.ride_a_t_a"]

In [11]:
# eta_edd_h3_hour_train, eta_edd_h3_hour_test, ata_train, ata_test = train_test_split(eta_edd_h3_hour, ata, test_size=0.05, random_state=73)
# print(len(eta_edd_h3_hour_train))
# print(len(eta_edd_h3_hour_test))

In [12]:
# dummy_train_rides = pd.get_dummies(eta_edd_h3_hour_train, prefix={'source_h3_4':'source_h3_4',
#                                                        'dest_h3_4':'dest_h3_4'},
#                           drop_first=True)
# dummy_train_rides.describe()

In [13]:
# geo_noise = np.count_nonzero(dummy_train_rides, axis=0) < 10
#
# cols = dummy_train_rides.columns
# for col, noise in zip(cols, geo_noise):
#     if noise:
#         # DOESN'T REINDEX
#         eta_edd_h3_hour_train = eta_edd_h3_hour_train[dummy_train_rides[col] == 0]
#         ata_train = ata_train[dummy_train_rides[col] == 0]
#
# eta_edd_h3_hour_train.describe()

In [14]:
# print(np.count_nonzero(dummy_train_rides, axis=0))
# print(dummy_train_rides.columns)

In [15]:
# ohe = ColumnTransformer(
#     [('OHE', OneHotEncoder(handle_unknown='ignore', sparse=False),['source_h3_4', 'dest_h3_4'])],
#     remainder = 'passthrough'
#     ).fit(eta_edd_h3_hour_train)

In [16]:
# eta_edd_h3_hour_train_transformed = ohe.transform(eta_edd_h3_hour_train)

In [17]:
# eta_edd_h3_hour_test_transformed = ohe.transform(eta_edd_h3_hour_test)

In [18]:
# reg = LinearRegression().fit(eta_edd_h3_hour_train_transformed, ata_train)

In [19]:
# print(reg.coef_)
# print(reg.intercept_)

In [20]:
# ata_train_pred = reg.predict(eta_edd_h3_hour_train_transformed)
# ata_test_pred = reg.predict(eta_edd_h3_hour_test_transformed)

In [21]:
# eta_edd_h3_hour_train_transformed

In [22]:
# print("ETA train MAE", mean_absolute_error(ata_train, eta_edd_h3_hour_train_transformed[:, 15]))
# print("prediction train MAE", mean_absolute_error(ata_train, ata_train_pred))
#
# print("ETA test MAE ", mean_absolute_error(ata_test, eta_edd_h3_hour_test_transformed[:, 15]))
# print("prediction test MAE", mean_absolute_error(ata_test, ata_test_pred))
#
#
# print("ETA train MSE", mean_squared_error(ata_train, eta_edd_h3_hour_train_transformed[:, 15]))
# print("prediction train MSE", mean_squared_error(ata_train, ata_train_pred))
#
# print("ETA test MSE ", mean_squared_error(ata_test, eta_edd_h3_hour_test_transformed[:, 15]))
# print("prediction test MSE", mean_squared_error(ata_test, ata_test_pred))
#
#
# print("ETA train explained_variance_score", explained_variance_score(ata_train, eta_edd_h3_hour_train_transformed[:, 15]))
# print("prediction train explained_variance_score", explained_variance_score(ata_train, ata_train_pred))
#
# print("ETA test explained_variance_score ", explained_variance_score(ata_test, eta_edd_h3_hour_test_transformed[:, 15]))
# print("prediction test explained_variance_score", explained_variance_score(ata_test, ata_test_pred))
#
#
# print("ETA train median_absolute_error", median_absolute_error(ata_train, eta_edd_h3_hour_train_transformed[:, 15]))
# print("prediction train median_absolute_error", median_absolute_error(ata_train, ata_train_pred))
#
# print("ETA test median_absolute_error ", median_absolute_error(ata_test, eta_edd_h3_hour_test_transformed[:, 15]))
# print("prediction test median_absolute_error", median_absolute_error(ata_test, ata_test_pred))
#
#
# print("ETA train r2_score", r2_score(ata_train, eta_edd_h3_hour_train_transformed[:, 15]))
# print("prediction train r2_score", r2_score(ata_train, ata_train_pred))
#
# print("ETA test r2_score ", r2_score(ata_test, eta_edd_h3_hour_test_transformed[:, 15]))
# print("prediction test r2_score", r2_score(ata_test, ata_test_pred))
#
#
# print("ETA train MAPE", mean_absolute_percentage_error(ata_train, eta_edd_h3_hour_train_transformed[:, 15]))
# print("prediction train MAPE", mean_absolute_percentage_error(ata_train, ata_train_pred))
#
# print("ETA test MAPE ", mean_absolute_percentage_error(ata_test, eta_edd_h3_hour_test_transformed[:, 15]))
# print("prediction test MAPE", mean_absolute_percentage_error(ata_test, ata_test_pred))

In [23]:
rides_p4 = rides[rides['eta'] > 1800]
rides_p4

eta   ata  a_t_a_result.ride_a_t_a           created_at  source_lat  \
7       3254  4100                     3942  2022-10-04 09:56:09   35.740150   
10      2188  2162                     2150  2022-10-04 09:21:41   35.762886   
30      2693  2828                     2620  2022-10-04 15:45:12   35.641914   
41      2151  3251                     3135  2022-10-04 10:15:55   35.665176   
48      2009  2147                     2136  2022-10-04 10:02:15   35.740749   
...      ...   ...                      ...                  ...         ...   
122075  2566  2938                     2961  2022-10-04 16:29:02   35.644901   
122081  1952  4446                     4336  2022-10-04 18:10:56   35.766682   
122090  4909  9081                     9155  2022-10-04 17:03:03   35.743797   
122093  1839  1740                     1747  2022-10-04 20:31:15   35.768658   
122094  2553  3771                     3732  2022-10-04 18:12:30   35.807266   

        source_lng  destination_lat  destination_lng      e_d_d  \
7        51.135941        35.775536        51.452332  40.798000   
10       51.316708        35.759953        51.409832  15.738000   
30       51.423805        35.805260        51.522381  28.052000   
41       51.352268        35.754646        51.410664  16.480000   
48       51.259422        35.733589        51.406292  19.128000   
...            ...              ...              ...        ...   
122075   51.301132        35.681496        51.019985  33.886002   
122081   51.477768        35.761921        51.405621   8.847000   
122090   51.366341        36.045437        50.544521  92.845001   
122093   51.477840        35.721954        51.516163  12.486000   
122094   51.428707        35.759602        51.334877  15.642000   

            clickhouse_time      source_h3_4        dest_h3_4  hour  
7       2022-10-04 11:10:44  842cf3dffffffff  842cf31ffffffff     9  
10      2022-10-04 10:01:25  842cf31ffffffff  842cf31ffffffff     9  
30      2022-10-04 17:19:29  842cf31ffffffff  842cf31ffffffff    15  
41      2022-10-04 11:19:05  842cf31ffffffff  842cf31ffffffff    10  
48      2022-10-04 10:42:07  842cf31ffffffff  842cf31ffffffff    10  
...                     ...              ...              ...   ...  
122075  2022-10-04 18:36:45  842cf31ffffffff  842cf3dffffffff    16  
122081  2022-10-04 20:26:34  842cf31ffffffff  842cf31ffffffff    18  
122090  2022-10-04 20:39:49  842cf31ffffffff  842cf07ffffffff    17  
122093  2022-10-04 21:31:44  842cf31ffffffff  842cf31ffffffff    20  
122094  2022-10-04 19:55:13  842cf31ffffffff  842cf31ffffffff    18  

[16126 rows x 13 columns]

In [24]:
rides_p4.describe()

eta           ata  a_t_a_result.ride_a_t_a    source_lat  \
count  16126.000000  16126.000000             16126.000000  16126.000000   
mean    2555.397247   3570.344227              3563.611993     35.695432   
std      692.453222   1757.983104              1711.870353      0.095370   
min     1801.000000    515.000000               461.000000     35.210945   
25%     2041.000000   2353.250000              2364.000000     35.659060   
50%     2374.000000   3051.000000              3049.000000     35.723452   
75%     2869.000000   4230.750000              4221.750000     35.759588   
max     8821.000000  17940.000000             10793.000000     35.831814   

         source_lng  destination_lat  destination_lng         e_d_d  \
count  16126.000000     16126.000000     16126.000000  16126.000000   
mean      51.398392        35.701529        51.355102     29.029813   
std        0.137800         0.103537         0.186716     16.590768   
min       50.901119        34.558254        49.693703      5.375000   
25%       51.330444        35.666199        51.303111     17.631500   
50%       51.406178        35.722916        51.396646     23.852500   
75%       51.462046        35.762365        51.454096     36.397749   
max       52.782028        36.312389        52.771801    230.001007   

               hour  
count  16126.000000  
mean      14.508682  
std        4.650957  
min        0.000000  
25%       10.000000  
50%       16.000000  
75%       18.000000  
max       23.000000

In [25]:
p4_eta_edd_h3_hour = rides_p4[["eta", "e_d_d", "source_h3_4", "dest_h3_4", "hour"]]
p4_ata = rides_p4["a_t_a_result.ride_a_t_a"]

In [26]:
p4_eta_edd_h3_hour_train, p4_eta_edd_h3_hour_test, p4_ata_train, p4_ata_test = train_test_split(p4_eta_edd_h3_hour, p4_ata, test_size=0.05, random_state=73)
print(len(p4_eta_edd_h3_hour_train))
print(len(p4_eta_edd_h3_hour_test))

15319
807


In [27]:
p4_dummy_train_rides = pd.get_dummies(p4_eta_edd_h3_hour_train, prefix={'source_h3_4': 'source_h3_4',
                                                             'dest_h3_4': 'dest_h3_4'},
                                   drop_first=True)
p4_dummy_train_rides.describe()

eta         e_d_d          hour  source_h3_4_842cd59ffffffff  \
count  15319.000000  15319.000000  15319.000000                 15319.000000   
mean    2555.642927     29.056679     14.514981                     0.001763   
std      692.766737     16.625739      4.648546                     0.041947   
min     1801.000000      5.375000      0.000000                     0.000000   
25%     2040.000000     17.648000     10.000000                     0.000000   
50%     2376.000000     23.875000     16.000000                     0.000000   
75%     2868.000000     36.408501     18.000000                     0.000000   
max     8821.000000    230.001007     23.000000                     1.000000   

       source_h3_4_842cd5bffffffff  source_h3_4_842cf31ffffffff  \
count                 15319.000000                 15319.000000   
mean                      0.000131                     0.840003   
std                       0.011426                     0.366616   
min                       0.000000                     0.000000   
25%                       0.000000                     1.000000   
50%                       0.000000                     1.000000   
75%                       0.000000                     1.000000   
max                       1.000000                     1.000000   

       source_h3_4_842cf33ffffffff  source_h3_4_842cf35ffffffff  \
count                 15319.000000                 15319.000000   
mean                      0.021085                     0.056727   
std                       0.143672                     0.231328   
min                       0.000000                     0.000000   
25%                       0.000000                     0.000000   
50%                       0.000000                     0.000000   
75%                       0.000000                     0.000000   
max                       1.000000                     1.000000   

       source_h3_4_842cf37ffffffff  source_h3_4_842cf3dffffffff  ...  \
count                 15319.000000                 15319.000000  ...   
mean                      0.025459                     0.054246  ...   
std                       0.157518                     0.226511  ...   
min                       0.000000                     0.000000  ...   
25%                       0.000000                     0.000000  ...   
50%                       0.000000                     0.000000  ...   
75%                       0.000000                     0.000000  ...   
max                       1.000000                     1.000000  ...   

       dest_h3_4_842cf0dffffffff  dest_h3_4_842cf21ffffffff  \
count               15319.000000               15319.000000   
mean                    0.000065                   0.000065   
std                     0.008080                   0.008080   
min                     0.000000                   0.000000   
25%                     0.000000                   0.000000   
50%                     0.000000                   0.000000   
75%                     0.000000                   0.000000   
max                     1.000000                   1.000000   

       dest_h3_4_842cf23ffffffff  dest_h3_4_842cf27ffffffff  \
count               15319.000000               15319.000000   
mean                    0.000065                   0.001110   
std                     0.008080                   0.033295   
min                     0.000000                   0.000000   
25%                     0.000000                   0.000000   
50%                     0.000000                   0.000000   
75%                     0.000000                   0.000000   
max                     1.000000                   1.000000   

       dest_h3_4_842cf31ffffffff  dest_h3_4_842cf33ffffffff  \
count               15319.000000               15319.000000   
mean                    0.756512                   0.018082   
std                     0.429201                   0.133253   
min                     0.000000                  

In [30]:
p4_geo_noise = np.count_nonzero(p4_dummy_train_rides, axis=0) < 11

p4_cols = p4_dummy_train_rides.columns
for col, noise in zip(p4_cols, p4_geo_noise):
    if noise:
        # DOESN'T REINDEX
        p4_eta_edd_h3_hour_train = p4_eta_edd_h3_hour_train[p4_dummy_train_rides[col] == 0]
        p4_ata_train = p4_ata_train[p4_dummy_train_rides[col] == 0]

p4_eta_edd_h3_hour_train.describe()

/var/folders/yq/707ysz_j3jlggmtk5clx13rm0000gn/T/ipykernel_21386/4019435953.py:7: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  p4_eta_edd_h3_hour_train = p4_eta_edd_h3_hour_train[p4_dummy_train_rides[col] == 0]


eta         e_d_d          hour
count  15291.000000  15291.000000  15291.000000
mean    2551.027533     28.919506     14.514943
std      679.590029     16.156415      4.650037
min     1801.000000      5.375000      0.000000
25%     2040.000000     17.635000     10.000000
50%     2375.000000     23.850000     16.000000
75%     2866.000000     36.341000     18.000000
max     7752.000000    170.723999     23.000000

In [31]:
print(np.count_nonzero(p4_dummy_train_rides, axis=0))
print(p4_dummy_train_rides.columns)

[15319 15319 15261    27     2 12868   323   869   390   831    10     1
    30     1    10     1    59     1     1     1    17 11589   277   734
   308   263  2011]
Index(['eta', 'e_d_d', 'hour', 'source_h3_4_842cd59ffffffff',
       'source_h3_4_842cd5bffffffff', 'source_h3_4_842cf31ffffffff',
       'source_h3_4_842cf33ffffffff', 'source_h3_4_842cf35ffffffff',
       'source_h3_4_842cf37ffffffff', 'source_h3_4_842cf3dffffffff',
       'dest_h3_4_842cd4bffffffff', 'dest_h3_4_842cd4dffffffff',
       'dest_h3_4_842cd59ffffffff', 'dest_h3_4_842cd5bffffffff',
       'dest_h3_4_842cf01ffffffff', 'dest_h3_4_842cf05ffffffff',
       'dest_h3_4_842cf07ffffffff', 'dest_h3_4_842cf0dffffffff',
       'dest_h3_4_842cf21ffffffff', 'dest_h3_4_842cf23ffffffff',
       'dest_h3_4_842cf27ffffffff', 'dest_h3_4_842cf31ffffffff',
       'dest_h3_4_842cf33ffffffff', 'dest_h3_4_842cf35ffffffff',
       'dest_h3_4_842cf37ffffffff', 'dest_h3_4_842cf39ffffffff',
       'dest_h3_4_842cf3dffffffff'],
      dt

In [32]:
p4_ohe = ColumnTransformer(
    [('OHE', OneHotEncoder(handle_unknown='ignore', sparse=False), ['source_h3_4', 'dest_h3_4'])],
    remainder='passthrough'
).fit(p4_eta_edd_h3_hour_train)

In [33]:
p4_eta_edd_h3_hour_train_transformed = p4_ohe.transform(p4_eta_edd_h3_hour_train)
p4_eta_edd_h3_hour_test_transformed = p4_ohe.transform(p4_eta_edd_h3_hour_test)

In [34]:
p4_reg = LinearRegression().fit(p4_eta_edd_h3_hour_train_transformed, p4_ata_train)
print(p4_reg.coef_)
print(p4_reg.intercept_)

[ -568.1319409    100.32346249   284.75895446   368.20769552
   -12.31539245  -112.38082805   -60.46195107 -1690.78615088
   545.87476188   506.40926454 -1154.80837767   441.70157177
   605.57939807    33.24827462   162.64616485   429.57583433
   120.5592585      2.14661424   -21.02859013    20.04972859]
-2211.49105049447


In [35]:
p4_ata_train_pred = p4_reg.predict(p4_eta_edd_h3_hour_train_transformed)
p4_ata_test_pred = p4_reg.predict(p4_eta_edd_h3_hour_test_transformed)

In [36]:
p4_eta_edd_h3_hour_train_transformed

array([[0.00000000e+00, 0.00000000e+00, 1.00000000e+00, ...,
        2.14500000e+03, 1.09860001e+01, 1.80000000e+01],
       [0.00000000e+00, 0.00000000e+00, 1.00000000e+00, ...,
        2.00700000e+03, 1.75119991e+01, 1.50000000e+01],
       [0.00000000e+00, 0.00000000e+00, 1.00000000e+00, ...,
        2.47600000e+03, 1.22819996e+01, 1.90000000e+01],
       ...,
       [0.00000000e+00, 0.00000000e+00, 1.00000000e+00, ...,
        2.06200000e+03, 1.51330004e+01, 1.90000000e+01],
       [0.00000000e+00, 0.00000000e+00, 1.00000000e+00, ...,
        2.39000000e+03, 2.11159992e+01, 2.10000000e+01],
       [0.00000000e+00, 0.00000000e+00, 1.00000000e+00, ...,
        1.87300000e+03, 2.50639992e+01, 1.30000000e+01]])

In [37]:
print("ETA train MAE", mean_absolute_error(p4_ata_train, p4_eta_edd_h3_hour_train_transformed[:, 17]))
print("prediction train MAE", mean_absolute_error(p4_ata_train, p4_ata_train_pred))

print("ETA test MAE ", mean_absolute_error(p4_ata_test, p4_eta_edd_h3_hour_test_transformed[:, 17]))
print("prediction test MAE", mean_absolute_error(p4_ata_test, p4_ata_test_pred))

print("ETA train MSE", mean_squared_error(p4_ata_train, p4_eta_edd_h3_hour_train_transformed[:, 17]))
print("prediction train MSE", mean_squared_error(p4_ata_train, p4_ata_train_pred))

print("ETA test MSE ", mean_squared_error(p4_ata_test, p4_eta_edd_h3_hour_test_transformed[:, 17]))
print("prediction test MSE", mean_squared_error(p4_ata_test, p4_ata_test_pred))

print("ETA train explained_variance_score", explained_variance_score(p4_ata_train, p4_eta_edd_h3_hour_train_transformed[:, 17]))
print("prediction train explained_variance_score", explained_variance_score(p4_ata_train, p4_ata_train_pred))

print("ETA test explained_variance_score ", explained_variance_score(p4_ata_test, p4_eta_edd_h3_hour_test_transformed[:, 17]))
print("prediction test explained_variance_score", explained_variance_score(p4_ata_test, p4_ata_test_pred))

print("ETA train median_absolute_error", median_absolute_error(p4_ata_train, p4_eta_edd_h3_hour_train_transformed[:, 17]))
print("prediction train median_absolute_error", median_absolute_error(p4_ata_train, p4_ata_train_pred))

print("ETA test median_absolute_error ", median_absolute_error(p4_ata_test, p4_eta_edd_h3_hour_test_transformed[:, 17]))
print("prediction test median_absolute_error", median_absolute_error(p4_ata_test, p4_ata_test_pred))

print("ETA train r2_score", r2_score(p4_ata_train, p4_eta_edd_h3_hour_train_transformed[:, 17]))
print("prediction train r2_score", r2_score(p4_ata_train, p4_ata_train_pred))

print("ETA test r2_score ", r2_score(p4_ata_test, p4_eta_edd_h3_hour_test_transformed[:, 17]))
print("prediction test r2_score", r2_score(p4_ata_test, p4_ata_test_pred))

print("ETA train MAPE", mean_absolute_percentage_error(p4_ata_train, p4_eta_edd_h3_hour_train_transformed[:, 17]))
print("prediction train MAPE", mean_absolute_percentage_error(p4_ata_train, p4_ata_train_pred))

print("ETA test MAPE ", mean_absolute_percentage_error(p4_ata_test, p4_eta_edd_h3_hour_test_transformed[:, 17]))
print("prediction test MAPE", mean_absolute_percentage_error(p4_ata_test, p4_ata_test_pred))

ETA train MAE 1096.6753645935516
prediction train MAE 856.3233735844267
ETA test MAE  1017.3717472118959
prediction test MAE 790.7508282643527
ETA train MSE 2879023.7464521616
prediction train MSE 1504965.9729127127
ETA test MSE  2307514.3531598514
prediction test MSE 1162933.5244844772
ETA train explained_variance_score 0.3672894395217836
prediction train explained_variance_score 0.48689754777100325
ETA test explained_variance_score  0.4237578642132125
prediction test explained_variance_score 0.5322049174080762
ETA train median_absolute_error 603.0
prediction train median_absolute_error 622.823281440923
ETA test median_absolute_error  585.0
prediction test median_absolute_error 588.8370798044843
ETA train r2_score 0.018426880794469414
prediction train r2_score 0.48689754777100325
ETA test r2_score  0.06591351865297645
prediction test r2_score 0.5292421551187003
ETA train MAPE 0.24710578169673528
prediction train MAPE 0.2507910410605186
ETA test MAPE  0.23854190142192694
prediction tes